Judyta Bąkowska, Karolina Źróbek

In [31]:
!pip3 install oracledb folium geojson shapely pandas

  Using cached pandas-2.2.2-cp39-cp39-macosx_10_9_x86_64.whl (12.6 MB)
  Using cached tzdata-2024.1-py2.py3-none-any.whl (345 kB)
  Using cached pytz-2024.1-py2.py3-none-any.whl (505 kB)
You should consider upgrading via the '/Volumes/SANDISK/vnav/venv/bin/python3 -m pip install --upgrade pip' command.


In [63]:
import oracledb
import folium
import geojson

from shapely.wkt import dumps, loads

# Definicja i test połączenia

In [64]:
cs = oracledb.makedsn("dbmanage.lab.ii.agh.edu.pl", 1521, sid="DBMANAGE")

un = "student"
pw = "stu638dent"

connection = oracledb.connect(user=un, password=pw, dsn=cs)

In [65]:
print(connection)

<oracledb.Connection to student@(DESCRIPTION=(ADDRESS=(PROTOCOL=TCP)(HOST=dbmanage.lab.ii.agh.edu.pl)(PORT=1521))(CONNECT_DATA=(SID=DBMANAGE)))>


# Wybór schematu US_SPAT

In [66]:
q = """ALTER SESSION SET CURRENT_SCHEMA = US_SPAT"""

cursor = connection.cursor()

cursor.execute(q)

In [67]:
def OutputTypeHandler(cursor, name, defaultType, size, precision, scale):
    if defaultType == oracledb.CLOB:
        return cursor.var(oracledb.LONG_STRING, arraysize = cursor.arraysize)
    
connection.outputtypehandler = OutputTypeHandler    

### Funkcje pomocnicze

In [68]:
import pandas as pd

def execute_query(query):
    cursor = connection.cursor()
    cursor.execute(query)
    col_names = [row[0] for row in cursor.description]
    rows = cursor.fetchall()
    df = pd.DataFrame(rows, columns=col_names)
    return df


In [69]:
def show_on_map(query, style= {'fillColor': 'cyan', 'color': 'yellow', 'fillOpacity': '0.8'}, m_map = None):
    rows = loads(cursor.execute(query).fetchall())
    
    m_list = []
    
    if(m_map == None):
        m_map = folium.Map()

    for row in rows:
        geo_data = geojson.Feature(geometry=row[0], properties={})
        m_list.append(geo_data)
    
    feature_collection = geojson.FeatureCollection(m_list)
    folium.GeoJson(feature_collection, style_function=lambda x:style).add_to(m_map)  
     
    return m_map 

# Zadanie 7 cz.2 
Dodatkowo:

a)     Oblicz odległość między miastem Tampa a drogą I4

b)    Jaka jest odległość z między stanem Nowy Jork a  Florydą

c)     Jaka jest odległość z między miastem Nowy Jork a  Florydą

d)    Podaj 3 parki narodowe do których jest najbliżej z Nowego Jorku, oblicz odległości do tych parków

e)    Przetestuj działanie funkcji

    a.     sdo_intersection, sdo_union, sdo_difference
    
    b.     sdo_buffer
    
    c.     sdo_centroid, sdo_mbr, sdo_convexhull, sdo_simplify


### Odległość między miastem Tampa a drogą I4

In [104]:
query = """

SELECT SDO_GEOM.SDO_DISTANCE ( c.location, i.geom, 0.5) distance
FROM us_interstates i, us_cities c
WHERE c.city = 'Tampa' and i.interstate = 'I4'

"""
execute_query(query)

DISTANCE
0  3103.911721

### Jaka jest odległość z między stanem Nowy Jork a  Florydą

In [101]:
query = """

SELECT SDO_GEOM.SDO_DISTANCE ( s1.geom, s2.geom, 0.5) distance
FROM us_states s1, us_states s2
WHERE s1.state = 'Florida' and s2.state = 'New York'

"""
execute_query(query)

DISTANCE
0  1.256584e+06

### Jaka jest odległość z między miastem Nowy Jork a  Florydą

In [105]:
query = """

SELECT SDO_GEOM.SDO_DISTANCE ( c.location, s2.geom, 0.5) distance
FROM us_cities c, us_states s2
WHERE c.city = 'New York' and s2.state = 'Florida'

"""
execute_query(query)

DISTANCE
0  1.296591e+06

### Podaj 3 parki narodowe do których jest najbliżej z Nowego Jorku, oblicz odległości do tych parków

In [12]:
query = """

SELECT p.name, SDO_GEOM.SDO_DISTANCE ( c.location, p.geom, 0.5) distance
FROM us_parks p, us_cities c 
WHERE c.city = 'New York'
AND sdo_nn(c.location, p.geom, 'sdo_num_res=3') = 'TRUE'
ORDER BY distance 
FETCH FIRST 3 ROW ONLY

"""
execute_query(query)

NAME     DISTANCE
0  Institute Park  1539.893923
1   Prospect Park  1718.069260
2  Thompkins Park  2135.556723

### Przetestuj działanie funkcji
`sdo_intersection`: Funkcja sdo_intersection oblicza przecięcie dwóch geometrii. Wynikiem jest geometria będąca wspólnym obszarem dwóch przecinających się obiektów przestrzennych.

`sdo_union`: Funkcja sdo_union oblicza sumę dwóch geometrii. Wynikiem jest geometria obejmująca obszar obu obiektów przestrzennych.

`sdo_difference`: Funkcja sdo_difference oblicza różnicę między dwoma geometriami. 
Wynikiem jest geometria będąca obszarem, który jest częścią pierwszego obiektu przestrzennego, ale nie jest częścią drugiego.

`sdo_buffer`: Funkcja sdo_buffer tworzy bufor wokół danej geometrii. Bufor jest obszarem, który znajduje się w określonej odległości od krawędzi geometrii wejściowej.

`sdo_centroid`: Funkcja sdo_centroid oblicza centroid danej geometrii. Centroid jest punktem, który jest środkiem ciężkości geometrii.

`sdo_mbr`: Funkcja sdo_mbr oblicza najmniejszy prostokąt otaczający (MBR - Minimum Bounding Rectangle) danej geometrii. MBR to prostokąt o najmniejszym polu, który otacza całą geometrię.

`sdo_convexhull`: Funkcja sdo_convexhull oblicza otoczkę wypukłą danej geometrii. Otoczka wypukła to najmniejszy obszar wypukły, który zawiera całą geometrię.

`sdo_simplify`: Funkcja sdo_simplify upraszcza geometrię, usuwając zbędne detale z jej kształtu. Parametr tolerancji określa, jak bardzo geometry ma być uproszczona.

In [135]:
## Parki przecinajce sie ze stanem Wyoming - wybierzmy 3 o najwiekszej powierzchni
# i połaczymy je w jeden geom za pomoca union
query = """ SELECT p.name, SDO_GEOM.SDO_AREA(p.geom) as area
FROM us_parks p, us_states s
WHERE s.state = 'Wyoming'
AND SDO_ANYINTERACT (p.geom, s.geom ) = 'TRUE'
ORDER BY area DESC
FETCH FIRST 3 ROW ONLY
"""
execute_query(query)


NAME          AREA
0     Shoshone NF  9.866570e+09
1  Yellowstone NP  8.895585e+09
2     Gallatin NF  8.704383e+09

In [142]:
query_mega_park = """ 
SELECT 
sdo_util.to_wktgeometry(
SDO_AGGR_UNION(SDOAGGRTYPE(p.geom, 0.05)))
AS union_geom
FROM us_parks p, us_states s
WHERE s.state = 'Wyoming'
  AND SDO_ANYINTERACT(p.geom, s.geom) = 'TRUE'
  AND p.name IN (
    SELECT p.name
    FROM us_parks p, us_states s
    WHERE s.state = 'Wyoming'
      AND SDO_ANYINTERACT(p.geom, s.geom) = 'TRUE'
    ORDER BY SDO_GEOM.SDO_AREA(p.geom) DESC
    FETCH FIRST 3 ROWS ONLY
)

"""

query_wyoming = """
SELECT sdo_util.to_wktgeometry(s.geom)
FROM  us_states s
WHERE s.state = 'Wyoming'
"""
show_on_map(query_mega_park, {'color': 'green', 'fillColor': 'forest'},m_map = show_on_map(query_wyoming) )

#### sdo_intersection

In [148]:
query = """

WITH
mega_park AS (
    SELECT SDO_AGGR_UNION(SDOAGGRTYPE(p.geom, 0.05)) AS union_geom
    FROM us_parks p
    JOIN us_states s ON SDO_ANYINTERACT(p.geom, s.geom) = 'TRUE'
    WHERE s.state = 'Wyoming'
      AND p.name IN (
        SELECT p.name
        FROM us_parks p
        JOIN us_states s ON SDO_ANYINTERACT(p.geom, s.geom) = 'TRUE'
        WHERE s.state = 'Wyoming'
        ORDER BY SDO_GEOM.SDO_AREA(p.geom) DESC
        FETCH FIRST 3 ROWS ONLY
    )
),
wyoming_state AS (
    SELECT s.geom AS state_geom
    FROM us_states s
    WHERE s.state = 'Wyoming'
)
SELECT sdo_util.to_wktgeometry(
    sdo_geom.sdo_intersection(wyoming_state.state_geom, mega_park.union_geom, 0.05)
) AS intersection_geom
FROM wyoming_state, mega_park


"""

show_on_map(query)


### `sdo_difference`

In [149]:
query = """

WITH
mega_park AS (
    SELECT SDO_AGGR_UNION(SDOAGGRTYPE(p.geom, 0.05)) AS union_geom
    FROM us_parks p
    JOIN us_states s ON SDO_ANYINTERACT(p.geom, s.geom) = 'TRUE'
    WHERE s.state = 'Wyoming'
      AND p.name IN (
        SELECT p.name
        FROM us_parks p
        JOIN us_states s ON SDO_ANYINTERACT(p.geom, s.geom) = 'TRUE'
        WHERE s.state = 'Wyoming'
        ORDER BY SDO_GEOM.SDO_AREA(p.geom) DESC
        FETCH FIRST 3 ROWS ONLY
    )
),
wyoming_state AS (
    SELECT s.geom AS state_geom
    FROM us_states s
    WHERE s.state = 'Wyoming'
)
SELECT sdo_util.to_wktgeometry(
    sdo_geom.sdo_difference(wyoming_state.state_geom, mega_park.union_geom, 0.05)
) AS difference_geom
FROM wyoming_state, mega_park


"""

show_on_map(query)


### `sdo_buffer, sdo_centroid, sdo_mbr, sdo_convexhull
Na przykładzie parku Yellowstone
#### Legenda:

- <span style="color:red">sdo_simplify</span>
- <span style="color:blue">sdo_buffer</span>
- sdo_centroid - pinezka
- <span style="color:orange">sdo_mbr</span>
- <span style="color:purple">sdo_convexhull</span>



In [20]:
query_buffer = """
SELECT sdo_util.to_wktgeometry(sdo_geom.sdo_buffer(geom, 100))
FROM us_parks
WHERE name='Yellowstone NP'
"""

query_centroid = """
SELECT sdo_util.to_wktgeometry(sdo_geom.sdo_centroid(geom))
FROM us_parks
WHERE name='Yellowstone NP'
"""
query_mbr = """
SELECT sdo_util.to_wktgeometry(
    sdo_geom.sdo_mbr(geom)
)
FROM us_parks
WHERE name='Yellowstone NP'
"""
query_convexhull = """
SELECT sdo_util.to_wktgeometry(
    sdo_geom.sdo_convexhull(geom)
)
FROM us_parks
WHERE name='Yellowstone NP'
"""

query_simplify = """
SELECT sdo_util.to_wktgeometry(
    SDO_UTIL.SIMPLIFY(geom,
    60,
   0.5)
)
FROM us_parks
WHERE name='Yellowstone NP'
"""

styles = {
    'buffer': {'color': 'blue', 'fillColor': 'blue'},
    'centroid': {'color': 'green', 'fillColor': 'green'},
    'mbr': {'color': 'orange', 'fillColor': 'orange'},
    'convexhull': {'color': 'purple', 'fillColor': 'purple'},
    'simplify': {'color': 'red', 'fillColor': 'red'}
}


show_on_map(
    query_convexhull, style=styles['convexhull'], m_map=show_on_map(
        query_mbr, style=styles['mbr'], m_map=show_on_map(
            query_centroid, style=styles['centroid'], m_map=show_on_map(
                query_buffer, style=styles['buffer']
            )
        )
    )  
)



In [21]:
show_on_map(query_simplify, style=styles['simplify'])

## Zadanie 8

### Analiza 1: wyszukiwanie trasy z miasta do miasta

Punkty miast w bazie `US_SPAT` zazwyczaj nie sa zlokalizowane wewnatrz wieloktów (`geom'ów`) dróg.  
Dlatego aby uzyskać informację, jakie drogi dochodza do danego miasta posłużymy się przybliżeniem. 
Tworzymy zestawienie miast i dróg znajdujcych się w promieniu 10 mil. 
Użyjemy wyłcznie miast w stanie New York aby ograniczyć liczbe miast następujce wyszukiwanie tras w grafie  było możliwe. 

In [71]:
interstates_10miles = """
SELECT c.city, i.interstate
FROM us_cities c
JOIN us_interstates i ON sdo_within_distance(
    c.location,
    i.geom,
    'distance=10 unit=mile'
) = 'TRUE'
WHERE c.state_abrv = 'NY'
"""

interstates_10miles = execute_query(interstates_10miles)
interstates_10miles.head()

CITY INTERSTATE
0  Rochester       I390
1    Buffalo       I190
2   New York       I278
3    Yonkers       I278
4    Yonkers       I287

Na tej podstawie mozemy wyszukać dostępne trasy pomiędzy Nowym Yorkiem a Buffalo:

In [51]:
df = interstates_10miles

# Function to find connections between two cities
def find_connections(city1, city2):
    connections = []
    interstates_city1 = df.loc[df['CITY'] == city1, 'INTERSTATE'].tolist()
    interstates_city2 = df.loc[df['CITY'] == city2, 'INTERSTATE'].tolist()
    for interstate1 in interstates_city1:
        for interstate2 in interstates_city2:
            connections.append([interstate1, interstate2])
    return connections

# Example cities
city1 = 'Buffalo'
city2 = 'New York'

# Find connections between the given cities
connections = find_connections(city1, city2)
for connection in connections:
    print(connection)


['I190', 'I278']
['I190', 'I478']
['I190', 'I495']
['I190', 'I678']
['I190', 'I78']
['I190', 'I87']
['I190', 'I95']
['I290', 'I278']
['I290', 'I478']
['I290', 'I495']
['I290', 'I678']
['I290', 'I78']
['I290', 'I87']
['I290', 'I95']
['I90', 'I278']
['I90', 'I478']
['I90', 'I495']
['I90', 'I678']
['I90', 'I78']
['I90', 'I87']
['I90', 'I95']
['I990', 'I278']
['I990', 'I478']
['I990', 'I495']
['I990', 'I678']
['I990', 'I78']
['I990', 'I87']
['I990', 'I95']


In [60]:
import random

def random_color():
    # Generate random values for red, green, and blue components
    r = random.randint(0, 255)
    g = random.randint(0, 255)
    b = random.randint(0, 255)

    # Convert the RGB values to hexadecimal format
    color_hex = '#{:02x}{:02x}{:02x}'.format(r, g, b)
    return color_hex

connections_vis = []
for connection in connections:
    query = """
         SELECT sdo_util.to_wktgeometry(geom)
         FROM us_interstates 
         WHERE interstate ="""
    interstates_str = ""
    for interstate in connection:
         interstates_str = interstates_str + "'" + interstate + "'" + " OR interstate="
    interstates_str = interstates_str[: -15]
    query  = query + interstates_str
         
    connections_vis.append(query)

routes_map = folium.Map()
for route in connections_vis:
    color = random_color()
    routes_map = show_on_map(route, style = {'color':color, 'fillColor': color }, m_map=routes_map)

cities_query = """
SELECT sdo_util.to_wktgeometry(location)
FROM US_CITIES 
WHERE city = 'New York' OR city = 'Buffalo'
"""
show_on_map(cities_query, m_map=routes_map)